In [ ]:
%matplotlib inline


# Canal

This case is a canal to test the damping condition in one direction


In [ ]:
import os, sys
import argparse
import numpy as np
import freshkiss3d as fk
import freshkiss3d.extra.plots as fk_plt
import math
import matplotlib.pyplot as plt
from matplotlib.pyplot import cm
import matplotlib.tri as mtri

os.system('rm -r outputs/hydrodynamic_vtk')
parser = argparse.ArgumentParser()
parser.add_argument('--nographics', action='store_true')
args = parser.parse_args()
#sphinx_gallery_thumbnail_number = 3


dir_path = os.path.abspath(os.path.dirname(sys.argv[0]))

## Parameters:




In [ ]:
mu = 12.5
sigma = 0.9
def topo_gaussian(x,y):
    topo = 1./(sigma * math.sqrt(2 * math.pi))*np.exp(-(x-mu)**2 / (2*sigma*sigma))
    return topo

## Time loop:



In [ ]:
FINAL_TIME = 20.

simutime = fk.SimuTime(final_time=FINAL_TIME, time_iteration_max=100000,
                       second_order=True)

## Mesh:



In [ ]:
triangular_mesh = fk.TriangularMesh.from_msh_file(dir_path+'/inputs/simple_canal.msh')   

if not args.nographics:
  fk_plt.plot_mesh(triangular_mesh)

## Layers:



In [ ]:
NL=1
layer = fk.Layer(NL, triangular_mesh, topography_funct=topo_gaussian)

## Primitives:




In [ ]:
def frees(x, y):
    if 0. <= x < 3.:
        free = 0.5
    else:
        free = 0.15
    return free


primitives = fk.Primitive(triangular_mesh, layer, free_surface_funct=frees)

if not args.nographics:
    fk_plt.plot_init_1d_slice(triangular_mesh, surf_xy=frees, topo_xy=topo_gaussian)
    plt.ylim(0, 1)
    plt.xlim(0, 25)

## Boundary conditions:



In [ ]:
case = 2
if case==1:
    slides = [fk.Slide(ref=r) for r in [1, 2, 3, 4]]
    damping_outs = []

if case==2:
    slides = [fk.Slide(ref=r) for r in [1, 3, 4]]
    damping_outs = [fk.DampingOut(ref=2, Kappa=1000., Theta=1000.)]

## Writter:



In [ ]:
times_figures = [1., 4., 8., 10., 12., 15., 19.]

create_figure_scheduler = fk.schedules(times=times_figures)

vtk_writer = fk.VTKWriter(triangular_mesh, scheduler=fk.schedules(times=times_figures),
                          scale_h=10)

## Problem definition:



In [ ]:
problem = fk.Problem(simutime, triangular_mesh, layer, primitives,
                     slides=slides,
                     damping_outs=damping_outs,
                     numerical_parameters={'space_second_order':True},
                     vtk_writer=vtk_writer,
                     custom_funct={'plot':fk_plt.plot_freesurface_3d},
                     custom_funct_scheduler=create_figure_scheduler)

## Problem solving:



In [ ]:
problem.solve()

if not args.nographics:
    plt.show()